# Capstone Project - The Battle of the Neighborhoods (Week 3 and 4)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

New York is famous for its Italian-American cuisines. In this project, We will try to determine the optimal location in the neighborhood of **New York City** to setup a new **Italian Restaurant** . The targeted audience thus is a group of stakeholders interested in opening up a restaurant in the New York City.

New York already has lot of places which are famous for different kinds of Italian foods.Thus our focus will be on **finding a location which is not yet much crowded with Italian Restaurants**. Since, we are also particularly interested in setting up an Italian restaurant, we will be looking at **areas with no Italian restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will leverage our data science powers to generate a few most promising neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

After specifying the problem statement, it is pretty clear that the factors which will affect while acquiring the data are as follows:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Italian restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:

* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **revese geocoding in Geocoder package**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of New York City center will be obtained using **Geocoder package** of well known Manhattan borough which is the major financial, commercial, and cultural center of NYC

### Neighborhood Candidates

We will create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around New York city center.

Let's first import all the necessary libraries fro this capstone project
 

In [1]:
import pandas as pd
import numpy as np
import requests
# from bs4 import BeautifulSoup

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.52         |     pyhd8ed1ab_0          35 KB  conda-forge
    geopy-2.2.0                |     pyhd8ed1ab_0          67 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         102 KB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.52-pyhd8ed1ab_0
  geopy              conda-forge/noarch::geopy-2.2.0-pyhd8ed1ab_0



geographiclib-1.52   | 35 KB     | ##################################### | 100% 
geopy-2.2.0          | 67 KB     | ##################################### | 100% 
Preparing transaction: done
Verifying transaction: done
Executing transa

Let's first find the latitude & longitude of New York city center, using specific, well known address and geocoder package

In [2]:
address = 'Manhattan, New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
manhattan_latitude = location.latitude
manhattan_longitude = location.longitude
print(manhattan_latitude,manhattan_longitude)

40.7896239 -73.9598939


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Manhattan. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [3]:
!pip install shapely
import shapely.geometry

!pip install pyproj
import pyproj

import math

def latlon_to_xy(lat, lon):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lat, lon)
    return xy[0], xy[1]

def xy_to_latlon(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    latlon = pyproj.transform(proj_xy, proj_latlon, x, y)
    return latlon[0],latlon[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

x, y = latlon_to_xy(manhattan_latitude, manhattan_longitude)
print('Manhattan UTM X={}, Y={}'.format(x, y))
la, lo = xy_to_latlon(x, y)
print('Manhattan latitude={}, longitude={}'.format(la, lo))

     |████████████████████████████████| 1.0MB 16.2MB/s eta 0:00:01
Manhattan UTM X=1272549.9243862303, Y=-8377976.635657506
Manhattan latitude=40.789623899999995, longitude=-73.9598939


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [4]:
nyc_center_x, nyc_center_y =  latlon_to_xy(manhattan_latitude,manhattan_longitude) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = nyc_center_x - 6000
x_step = 600
y_min = nyc_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(nyc_center_x, nyc_center_y, x, y)
        if (distance_from_center <= 6001):
            lat, lon = xy_to_latlon(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [5]:
!pip install folium

import folium

In [6]:
map_nyc = folium.Map(location=(manhattan_latitude,manhattan_longitude), zoom_start=13)
folium.Marker([manhattan_latitude,manhattan_longitude], popup='Manhattan').add_to(map_nyc)
for lat, lon in zip(latitudes, longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_nyc) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_nyc)
#     folium.Marker([lat, lon]).add_to(map_nyc)
map_nyc

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Manhattan. 

Let's now use Geocoder to get approximate addresses of those locations.

In [8]:
def get_address(latitude, longitude):
    locator = Nominatim(user_agent="myGeocoder")
    coordinates = (latitude, longitude)
    location = locator.reverse(coordinates)
    address= location.address
    return address
# address=get_address(43.2,-73)
# address

In [9]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', United States', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [10]:
addresses[150:170]

['316, East Madison Avenue, Cresskill, Bergen County, New Jersey, 07626',
 'Anderson Avenue, Demarest, Bergen County, New Jersey, 07624',
 '35, Halsey Lane, Closter, Bergen County, New Jersey, 07624',
 '3917, 14th Avenue, Borough Park, Brooklyn, Kings County, New York, 11218',
 'Bishop Ford Center Catholic High School, 19th Street, Windsor Terrace, Brooklyn, Kings County, New York, 11218',
 '133, Garfield Place, Park Slope, Brooklyn, Kings County, New York, 11215',
 'Revolutionary Garden, Willoughby Street, Fort Greene, Brooklyn, Kings County, New York, 11201',
 'Pier J, Railroad Avenue, Brooklyn Navy Yard, Brooklyn, Kings County, New York, 11251',
 '799, East 13th Street, East Village, Manhattan, New York County, New York, 10009',
 'East 34th Street/Midtown, FDR Drive Greenway, Murray Hill, Manhattan, New York County, New York, 10017-6927',
 'LinkNYC, East 58th Street, Manhattan Community Board 6, Manhattan, New York County, New York, 10022',
 'King Jagiello Monument, East Drive, Manh

Let's now arrange all this into a Pandas dataframe.

In [11]:
import pandas as pd

df_nyc = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_nyc.head(10)

Address   Latitude  Longitude  \
0  2101, 91st Street, Babbitt, North Bergen, Huds...  40.814656 -74.012769   
1  South Broad Avenue, Ridgefield, Bergen County,...  40.832223 -74.010517   
2  Palisades Park Sports Complex, Roosevelt Place...  40.849784 -74.008264   
3  New Jersey Turnpike, Teaneck Township, Bergen ...  40.867341 -74.006009   
4  882, Club Road, Colonial Village, Teaneck Town...  40.884892 -74.003753   
5  75, State Street, West Englewood, Teaneck Town...  40.902438 -74.001495   
6  40, West Broad Street, Bergenfield, Bergen Cou...  40.919980 -73.999236   
7  5318, Fairview Terrace, West New York, Hudson ...  40.781229 -74.011951   
8  595, 74th Street, North Bergen, Hudson County,...  40.798799 -74.009702   
9  Fairview Cemetery, Durham Avenue, Hudson Heigh...  40.816365 -74.007451   

              X             Y  Distance from center  
0  1.270750e+06 -8.383692e+06           5992.495307  
1  1.271350e+06 -8.383692e+06           5840.376700  
2  1.271950e+06 -8.383692e+06           5747.173218  
3  1.272550e+06 -8.383692e+06           5715.767665  
4  1.273150e+06 -8.383692e+06           5747.173218  
5  1.273750e+06 -8.383692e+06           5840.376700  
6  1.274350e+06 -8.383692e+06           5992.495307  
7  1.269850e+06 -8.383173e+06           5855.766389  
8  1.270450e+06 -8.383173e+06           5604.462508  
9  1.271050e+06 -8.383173e+06           5408.326913

...and let's now save/persist this data into local file.

In [12]:
df_nyc.to_pickle('./locations.pkl')    

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We are focusing on "food" venue category. We will not be considering venues like coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in our list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

Foursquare credentials are defined in hidden cell bellow.

In [76]:
# @hidden_cell
client_id = '4N3GTCFHDJAEQIOA2MY2HS3CBFZFGRXALWEMX0JERUTORJ0G' # your Foursquare ID
client_secret = '0JRWSQ5LWOSTKIZHZR4F2412BMDU3Z1MEIPSSXJPP4WJD01G' # your Foursquare Secret
version= '20180605' # Foursquare API version
limit = 100 # A default Foursquare API limit value
 

In [14]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', United States', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [15]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_res:
                x, y =latlon_to_xy(venue_latlon[0],venue_latlon[1])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, italian_restaurants, location_restaurants

restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
 

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [16]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 2221
Total number of Italian restaurants: 235
Percentage of Italian restaurants: 10.58%
Average number of restaurants in neighborhood: 5.387362637362638


The percentage of Italian restaurant is approximately 11% of the total restaurants in the neighborhood. This means we have got enough scope to setup an Italian restaurant in NYC. Let's explore more.

Let's print the names of all the restaurants present in the Manhattan neighborhood.


In [17]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4b8467ebf964a520953331e3', 'Panda Express', 40.81318359089419, -74.0119484449919, '2100 88th St (Tonnelle Ave), North Bergen, NJ 07047', 177, False, 1270747.4772926278, -8383589.518913799)
('4b934941f964a5209c3e34e3', "Applebee's Grill + Bar", 40.81353525, -74.01133241, '2100 88th St (Route 9), North Bergen, NJ 07047', 173, False, 1270786.5414400168, -8383531.338345344)
('5734a361498e7d192a4489be', '방가네', 40.834184, -74.009601, 'Ridgefield, NJ', 231, False, 1271448.4508708895, -8383624.674717551)
('5206c92311d29d0be0d49f5d', '푸른바다', 40.8338623046875, -74.00934600830078, 'Ridgefield, NJ', 349, False, 1271451.5086970064, -8383594.49120522)
('5734d634498e15f0e6d8f1b9', 'Arirang Kimchi', 40.835327, -74.00994, '1 Remsen Pl, Ridgefield, NJ 07657', 348, False, 1271464.4711339492, -8383674.151091746)
('4e485a9b52b1bac0d99088c6', 'Green Garden Restaurant', 40.88756, -74.005292, '949 Teaneck Rd, Teaneck, NJ 07666', 324, False, 1273151.7083749361,

Now, we will print all the Italian restaurants 

In [18]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('4c21516a13c00f471cd285de', 'Cafe Tivoli', 40.832835284386306, -74.00260246476847, '533 Shaler Blvd (Banta Pl), Ridgefield, NJ 07657', 250, True, 1271742.4182764748, -8382894.010856747)
('56ca2b9dcd10be26b99ca5c1', 'The Recipe', 40.923515, -73.996634, 'Bergenfield, NJ', 308, True, 1274572.9797546403, -8383473.863103222)
('4c423882e26920a12ec05fe7', "Foschini's Brick Oven Kitchen", 40.94049115459089, -73.99298333684223, '21 E Madison Ave, Dumont, NJ 07628', 183, True, 1275223.5032949026, -8383325.04851102)
('4c0308e6187ec928d229b57b', "Buongiorno's Ristorante", 40.938943, -73.994225, '86 Washington Ave, Dumont, NJ 07628', 217, True, 1275120.9155547367, -8383431.125017246)
('4b522521f964a5203d6b27e3', 'Trattoria La Sorrentina', 40.80177193590717, -74.00678327077871, '7831 Bergenline Ave (79th St), North Bergen, NJ 07047', 246, True, 1270671.6468953257, -8382914.1781215705)
('4a552b26f964a520c4b31fe3', 'Malatesta Trattoria', 40.7328

In [19]:
print('Restaurants around location')
print('---------------------------')
# input=location_restaurants
# print(len(input),len(input[0]) ) 
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Gramercy Tavern, Union Square Cafe, Sugarfish, Craft, Mari Vanna, Nana Thai Street, Rezdôra, Oceans
Restaurants around location 102: Margon, Tony's Di Napoli, OOTOYA 大戸屋 (OOTOYA), Hard Rock Cafe, Bubba Gump Shrimp Co., Paul's On Times Square, The Lambs Club, Royal Grill Halal Food
Restaurants around location 103: Dig Inn, Atlantic Grill, Boulud Sud, The Smith, Cafe Fiorello, Joanne Trattoria, Bar Boulud, The Grand Tier
Restaurants around location 104: Chinoise Laundromatte
Restaurants around location 105: 
Restaurants around location 106: Brownstone Pancake Factory, Duck King Chinese Cuisine, The Great Burrito, Roberto's II Ristorante, River Thai Food, Haifa Cafe And Grill, Emma Bistro, Park Bistro
Restaurants around location 107: Food For Life
Restaurants around location 108: Chipotle Mexican Grill, Hachi Sushi, Chillers Grill
Restaurants around location 109: 
Restaurants around location 110: Waff

Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [20]:
map_nyc = folium.Map(location=(manhattan_latitude,manhattan_longitude), zoom_start=13)
folium.Marker([manhattan_latitude,manhattan_longitude], popup='Manhattan').add_to(map_nyc)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_nyc)
map_nyc

So, now we have all the restaurants in area within few kilometers from Manhattan, and we know which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of New York City that have low restaurant density, particularly those with low number of Italian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from New York City center** (Manhattan). We have also **identified Italian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of New York City - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Italian restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [22]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_nyc['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_nyc.head(10)

Average number of restaurants in every area with radius=300m: 5.387362637362638


Address   Latitude  Longitude  \
0  2101, 91st Street, Babbitt, North Bergen, Huds...  40.814656 -74.012769   
1  South Broad Avenue, Ridgefield, Bergen County,...  40.832223 -74.010517   
2  Palisades Park Sports Complex, Roosevelt Place...  40.849784 -74.008264   
3  New Jersey Turnpike, Teaneck Township, Bergen ...  40.867341 -74.006009   
4  882, Club Road, Colonial Village, Teaneck Town...  40.884892 -74.003753   
5  75, State Street, West Englewood, Teaneck Town...  40.902438 -74.001495   
6  40, West Broad Street, Bergenfield, Bergen Cou...  40.919980 -73.999236   
7  5318, Fairview Terrace, West New York, Hudson ...  40.781229 -74.011951   
8  595, 74th Street, North Bergen, Hudson County,...  40.798799 -74.009702   
9  Fairview Cemetery, Durham Avenue, Hudson Heigh...  40.816365 -74.007451   

              X             Y  Distance from center  Restaurants in area  
0  1.270750e+06 -8.383692e+06           5992.495307                    2  
1  1.271350e+06 -8.383692e+06           5840.376700                    2  
2  1.271950e+06 -8.383692e+06           5747.173218                    0  
3  1.272550e+06 -8.383692e+06           5715.767665                    0  
4  1.273150e+06 -8.383692e+06           5747.173218                    0  
5  1.273750e+06 -8.383692e+06           5840.376700                    4  
6  1.274350e+06 -8.383692e+06           5992.495307                    0  
7  1.269850e+06 -8.383173e+06           5855.766389                    3  
8  1.270450e+06 -8.383173e+06           5604.462508                   11  
9  1.271050e+06 -8.383173e+06           5408.326913                    0

OK, now let's calculate the **distance to nearest Italian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [24]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_nyc['Distance to Italian restaurant'] = distances_to_italian_restaurant

In [25]:
df_nyc.head(10)

Address   Latitude  Longitude  \
0  2101, 91st Street, Babbitt, North Bergen, Huds...  40.814656 -74.012769   
1  South Broad Avenue, Ridgefield, Bergen County,...  40.832223 -74.010517   
2  Palisades Park Sports Complex, Roosevelt Place...  40.849784 -74.008264   
3  New Jersey Turnpike, Teaneck Township, Bergen ...  40.867341 -74.006009   
4  882, Club Road, Colonial Village, Teaneck Town...  40.884892 -74.003753   
5  75, State Street, West Englewood, Teaneck Town...  40.902438 -74.001495   
6  40, West Broad Street, Bergenfield, Bergen Cou...  40.919980 -73.999236   
7  5318, Fairview Terrace, West New York, Hudson ...  40.781229 -74.011951   
8  595, 74th Street, North Bergen, Hudson County,...  40.798799 -74.009702   
9  Fairview Cemetery, Durham Avenue, Hudson Heigh...  40.816365 -74.007451   

              X             Y  Distance from center  Restaurants in area  \
0  1.270750e+06 -8.383692e+06           5992.495307                    2   
1  1.271350e+06 -8.383692e+06           5840.376700                    2   
2  1.271950e+06 -8.383692e+06           5747.173218                    0   
3  1.272550e+06 -8.383692e+06           5715.767665                    0   
4  1.273150e+06 -8.383692e+06           5747.173218                    0   
5  1.273750e+06 -8.383692e+06           5840.376700                    4   
6  1.274350e+06 -8.383692e+06           5992.495307                    0   
7  1.269850e+06 -8.383173e+06           5855.766389                    3   
8  1.270450e+06 -8.383173e+06           5604.462508                   11   
9  1.271050e+06 -8.383173e+06           5408.326913                    0   

   Distance to Italian restaurant  
0                      782.152050  
1                      889.652732  
2                      824.917763  
3                     1135.560059  
4                     1439.738313  
5                      851.574992  
6                      312.271556  
7                      861.456321  
8                      340.646417  
9                      458.228077

In [27]:
print('Average distance to closest Italian restaurant from each area center:', df_nyc['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 629.120645306197


OK, so **on average Italian restaurant can be found within ~700m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

We will be downloading new york boroughs data by following the same procedure we did in one of the previous lab

In [28]:
 def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Data downloaded!


In [29]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of NYC boroughs** on our map and a few circles indicating distance of 1km, 2km and 3km from Manhattan.

In [33]:
from folium import plugins
from folium.plugins import HeatMap

map_nyc = folium.Map(location=(manhattan_latitude,manhattan_longitude), zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_nyc) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_nyc)
folium.Marker([manhattan_latitude,manhattan_longitude]).add_to(map_nyc)
folium.Circle([manhattan_latitude,manhattan_longitude], radius=1000, fill=False, color='white').add_to(map_nyc)
folium.Circle( [manhattan_latitude,manhattan_longitude], radius=2000, fill=False, color='white').add_to(map_nyc)
folium.Circle( [manhattan_latitude,manhattan_longitude], radius=3000, fill=False, color='white').add_to(map_nyc)
folium.GeoJson(newyork_data, style_function=boroughs_style, name='geojson').add_to(map_nyc)
map_nyc

Looks like a few pockets of low restaurant density closest to city center can be found **north-west, east, south-east and west from Manhattan**. 

Let's create another heatmap map showing **heatmap/density of Italian restaurants** only.

In [57]:
map_nyc = folium.Map(location=(manhattan_latitude,manhattan_longitude), zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_nyc) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_nyc )
folium.Marker([manhattan_latitude,manhattan_longitude]).add_to(map_nyc )
folium.Circle([manhattan_latitude,manhattan_longitude], radius=1000, fill=False, color='white').add_to(map_nyc )
folium.Circle([manhattan_latitude,manhattan_longitude], radius=2000, fill=False, color='white').add_to(map_nyc )
folium.Circle([manhattan_latitude,manhattan_longitude], radius=3000, fill=False, color='white').add_to(map_nyc )
folium.GeoJson(newyork_data, style_function=boroughs_style, name='geojson').add_to(map_nyc )
map_nyc

This map is not so 'hot' (Italian restaurants represent a subset of ~11% of all restaurants in NYC) but it also indicates higher density of existing Italian restaurants directly south and south-west from Manhattan, with closest pockets of **low Italian restaurant density positioned east, south-east, north, west, north-west from city center**.

Based on this we will now focus our analysis on areas * east, south-east, north, west, north-west from NYC center*  

OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant**.

In [46]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

restaurant_counts = []
italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(df_nyc['X'],df_nyc['Y']):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    italian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [68]:
df_nyc["Restaurants nearby"]= restaurant_counts
df_nyc["Distance to Italian restaurant"]=italian_distances
df_nyc.head()

Address   Latitude  Longitude  \
0  2101, 91st Street, Babbitt, North Bergen, Huds...  40.814656 -74.012769   
1  South Broad Avenue, Ridgefield, Bergen County,...  40.832223 -74.010517   
2  Palisades Park Sports Complex, Roosevelt Place...  40.849784 -74.008264   
3  New Jersey Turnpike, Teaneck Township, Bergen ...  40.867341 -74.006009   
4  882, Club Road, Colonial Village, Teaneck Town...  40.884892 -74.003753   

              X             Y  Distance from center  Restaurants in area  \
0  1.270750e+06 -8.383692e+06           5992.495307                    2   
1  1.271350e+06 -8.383692e+06           5840.376700                    2   
2  1.271950e+06 -8.383692e+06           5747.173218                    0   
3  1.272550e+06 -8.383692e+06           5715.767665                    0   
4  1.273150e+06 -8.383692e+06           5747.173218                    0   

   Distance to Italian restaurant  Restaurants nearby  
0                      782.152050                   2  
1                      889.652732                   3  
2                      824.917763                   0  
3                     1135.560059                   0  
4                     1439.738313                   1

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 400 meters**.

In [69]:
good_res_count = np.array((df_nyc['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_nyc['Distance to Italian restaurant']>=400)
print('Locations with no Italian restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_nyc[good_locations]

Locations with no more than two restaurants nearby: 218
Locations with no Italian restaurants within 400m: 249
Locations with both conditions met: 190


Let's see how this looks on a map.

In [70]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_nyc = folium.Map(location=[manhattan_latitude,manhattan_longitude], zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_nyc)
HeatMap(restaurant_latlons).add_to(map_nyc)
folium.Marker([manhattan_latitude,manhattan_longitude]).add_to(map_nyc)
folium.Circle([manhattan_latitude,manhattan_longitude], radius=1000, fill=False, color='white').add_to(map_nyc )
folium.Circle([manhattan_latitude,manhattan_longitude], radius=2000, fill=False, color='white').add_to(map_nyc )
folium.Circle([manhattan_latitude,manhattan_longitude], radius=3000, fill=False, color='white').add_to(map_nyc )
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_nyc) 
folium.GeoJson(newyork_data, style_function=boroughs_style, name='geojson').add_to(map_nyc)
map_nyc

Looking good. We now have a bunch of locations fairly close to Manhattan in the radius of 1km, 2km, and 3km, and we know that each of those locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 400m. Any of those locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.


Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [77]:
from sklearn.cluster import KMeans

number_of_clusters = 20

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_latlon(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_nyc = folium.Map(location=[manhattan_latitude,manhattan_longitude], zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_nyc)
HeatMap(restaurant_latlons).add_to(map_nyc)
folium.Circle([manhattan_latitude,manhattan_longitude], radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_nyc)
folium.Marker([manhattan_latitude,manhattan_longitude]).add_to(map_nyc)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=500, color="black", fill=True, fill_opacity=0.25).add_to(map_nyc) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_nyc)
folium.GeoJson(newyork_data, style_function=boroughs_style, name='geojson').add_to(map_nyc)
map_nyc 

Our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Stakeholders can explore the good locations we will suggest at the end.The address of those locations will be starting point fro their further exploration.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [78]:
map_nyc = folium.Map(location=[manhattan_latitude,manhattan_longitude], zoom_start=14)
folium.Marker( [manhattan_latitude,manhattan_longitude]).add_to(map_nyc)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_nyc)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_nyc)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_nyc) 
folium.GeoJson(newyork_data, style_function=boroughs_style, name='geojson').add_to(map_nyc)
map_nyc

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [79]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lat,lon in cluster_centers:
    addr = get_address(lat, lon).replace(', United States', '')
    candidate_area_addresses.append(addr)    
    x, y = latlon_to_xy(lat,lon)
    d = calc_xy_distance(x, y, nyc_center_x, nyc_center_y)
    print('{}{} => {:.1f}km from Manhattan'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

Vaccaro Drive, Cresskill, Bergen County, New Jersey, 07670 => 4.9km from Manhattan
West 79th Street Boat Basin, Henry Hudson Parkway, Upper West Side, Manhattan Community Board 7, Manhattan, New York County, New York, 10069 => 3.0km from Manhattan
11, Maujer Street, Williamsburg, Brooklyn, Kings County, New York, 11206 => 2.7km from Manhattan
2, Sunset Terrace, Tenafly, Bergen County, New Jersey, 07670 => 4.9km from Manhattan
Newkirk Plaza, Newkirk Avenue, Brooklyn Community District 17, Brooklyn, Kings County, New York, 11203 => 4.8km from Manhattan
27-02, 1st Street, Astoria, Queens, Queens County, New York, 11102 => 2.5km from Manhattan
2521, Palisade Avenue, The Bronx, Bronx County, New York, 10463 => 4.8km from Manhattan
Overpeck Golf Course, Overpeck Park Driveway, Leonia, Bergen County, New Jersey, 07605 => 5.0km from Manhattan
480, Golf Course Drive, Leonia, Bergen County, New Jersey, 07605 => 3.4km from Manhattan


This concludes our analysis. We have created 20 addresses representing centers of zones containing locations within 6km from Manhattan, with low number of restaurants and no Italian restaurants nearby. Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. 

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in New York City(~2300 in our initial area of interest which was 12x12km around Manhattan), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected in south-west and north-east and central part pf Manhattan. Thus, our focus shifted to the north-eastern and south-eastern parts.

We filtered the locations so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 20 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to New York City center but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify New York City areas close to center with low number of restaurants (particularly Italian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution from Foursquare data we have generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.